In [ ]:
from google.colab import drive
import pandas as pd
import numpy as np
from numpy import array
from numpy import asarray
from numpy import zeros
import nltk
from nltk.corpus import stopwords 
import re
import string
from itertools import groupby
from collections import Counter
import matplotlib.pyplot as plt
from scipy.sparse import hstack
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, precision_score
from sklearn.metrics import recall_score, f1_score
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
from numpy import savetxt

In [ ]:
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [ ]:
with open('/content/drive/My Drive/Data Files/code-mixed analysis data/POS Hindi English Code Mixed Tweets.tsv', 'r') as fp:
	  data = fp.readlines()
 

for i in range(len(data)):
    data[i] = data[i].strip('\n')
    data[i] = data[i].split('\t')
 

tweets = []
current_point = []

for token in data:
    if token[0] == '':
        if len(current_point) > 0:
            tweets.append(current_point)
            current_point = []
    else:
        current_point.append(token)

print(len(tweets))
print(tweets)
print(tweets[0])

tweets = np.array(tweets)
np.random.seed(52)
np.random.shuffle(tweets)
tweets = tweets.tolist()

1489
[[['Pak', 'rest', 'PROPN'], ['is', 'en', 'VERB'], ['in', 'en', 'ADP'], ['confused', 'en', 'ADJ'], ['state', 'en', 'NOUN'], ['of', 'en', 'ADP'], ['mind', 'en', 'VERB'], ['.', 'rest', 'X'], ['#SurgicalStrike', 'rest', 'X'], ['hui', 'hi', 'VERB'], ['ya', 'hi', 'CONJ'], ['nahi', 'hi', 'PART_NEG'], ['is', 'hi', 'DET'], ['par', 'hi', 'ADP'], ['contradictory', 'en', 'NOUN'], ['statements', 'en', 'NOUN'], ['aa', 'hi', 'VERB'], ['rahe', 'hi', 'VERB'], ['hain', 'hi', 'VERB'], ['.', 'rest', 'X'], ['Nahi', 'hi', 'PART_NEG'], ['huyi', 'hi', 'PART'], ['to', 'hi', 'PART'], ['tension', 'en', 'NOUN'], ['mai', 'hi', 'ADP'], ['kyon', 'hi', 'PRON_WH'], ['?', 'rest', 'X']], [['@ncpspeaks', 'rest', 'X'], ['former', 'en', 'ADJ'], ['Gen', 'en', 'NOUN'], ['.', 'rest', 'X'], ['V', 'rest', 'PROPN'], ['P', 'rest', 'PROPN'], ['Malik', 'rest', 'PROPN'], ['aur', 'hi', 'CONJ'], ['DGMO', 'rest', 'PROPN'], ['Vinod', 'rest', 'PROPN'], ['Bhatiya', 'rest', 'PROPN'], ['ne', 'hi', 'ADP'], ['kaha', 'hi', 'PRON_WH'], ['k

In [ ]:
# pos data
f = open('/content/drive/My Drive/Data Files/code-mixed analysis data/POS Hindi English Code Mixed Tweets.tsv', 'r')
tokens_list = []
tokens = []
languages_list = []
languages = []
pos_list = []
pos = []
for line in f:
    line = line.strip()
    line = line.split('\t')
    line = [token.strip() for token in line if token != '' and  token != ' ' and token != '\n']
    if len(line) == 0:
        tokens_list.append(tokens)
        languages_list.append(languages)
        pos_list.append(pos)
        tokens = []
        languages = []
        pos = []
    else:
        tokens.append(line[0])
        languages.append(line[1])
        pos.append(line[2])

In [ ]:
df = pd.DataFrame(data=np.array(tokens_list), columns=['Tokens'])
df['Languages'] = np.array(languages_list)
df['POS Tags'] = np.array(pos_list)
df

Tokens  ...                                           POS Tags
0     [Pak, is, in, confused, state, of, mind, ., #S...  ...  [PROPN, VERB, ADP, ADJ, NOUN, ADP, VERB, X, X,...
1     [@ncpspeaks, former, Gen, ., V, P, Malik, aur,...  ...  [X, ADJ, NOUN, X, PROPN, PROPN, PROPN, CONJ, P...
2     [Anyone, heard, of, hafiz, saeed, ,, salahuddi...  ...  [PRON, VERB, ADP, PROPN, PROPN, X, PROPN, CONJ...
3     [@ArvindKejriwal, Worldwide, #SurgicalStrike, ...  ...  [X, NOUN, X, NOUN, VERB, VERB, VERB, VERB, NOU...
4     [RT, @UsmanAQayyum, :, Pak, :, Acha, Dikao, Za...  ...  [X, X, X, PROPN, X, ADJ, PART, PART, NOUN, PRO...
...                                                 ...  ...                                                ...
1484  [#UriAttack, @narendramodi, @rajnathsingh, @ma...  ...  [X, X, X, X, NOUN, PRON_WH, ADV, PART, NOUN, V...
1485  [Dudh, mangoge, kheer, denge, kashmir, mango, ...  ...  [NOUN, VERB, NOUN, VERB, PROPN, VERB, VERB, CO...
1486  [Only, Mani, Shankar, Aiyars, of, the, world, ...  ...  [ADV, PROPN, PROPN, PROPN, ADP, DET, NOUN, VER...
1487  [RT, @PanditRamJoshi, :, We, can, arm, &, pay,...  ...  [X, X, X, PRON, VERB, VERB, CONJ, VERB, PROPN,...
1488  [-, RT, @javaidShaikh, :, Mr, SirJadejaaaa, An...  ...  [X, X, X, X, PROPN, PROPN, DET, ADJ, VERB, VER...

[1489 rows x 3 columns]

In [ ]:
# features for CRF (Conditonal Random Fields) model
# 1. The current token T, T after stripping all characters which are not in the Roman alphabet and converting to lowercase
# 2. the language tag of T
# 3. length of T
# 4. fraction of ASCII characters in T
# 5. affixes of length 1 to 3, padded with whitespace if needed
# 6. a binary feature indicating whether T is titlecased
# 7. a binary feature indicating whether there is a non alphabetic character in T
# 8. a binary feature indicating whether all characters in T are uppercase

In [ ]:
# length of T
def get_length(token):
    return len(token)

# fraction of ASCII characters in T
def get_ascii_fraction(token):
    count = 0
    for char in token:
        if ord(char) < 128:
            count = count + 1
    return count/len(token)

# fraction of vowels in T
def get_vowel_fraction(token):
    count = 0
    vowels = ['a', 'e', 'i', 'o', 'u']
    for char in token:
        if char in vowels:
            count = count + 1
    return count/len(token)

# stripping all characters which are not in the Roman alphabet and converting to lowercase
def clean(token):
    token_clean = ''.join([ch for ch in token if ch in 'asdfghjklqwertyuiopzxcvbnmQWERTYUIOPASDFGHJKLZXCVBNM']).lower()
    return token_clean

# check if word in title cased
def check_title_cased(token):
    return token.istitle()

# check all characters in T are uppercase
def check_all_uppercase(token):
    return all(char.isupper() for char in token)

# check any character in T is uppercase
def check_any_uppercase(token):
    return any(char.isupper() for char in token)

# check for special characters
def check_any_special(token):
    return any(ord(char) > 32 and ord(char) < 65 for char in token)

In [ ]:
# feature vector
def word_features(sentence, i):
    word = sentence[i][0]
    language = sentence[i][1]

    features = {'word': word, 'word_clean': clean(word), 'language': language, 'is_title': check_title_cased(word),
                'word_length': get_length(word), 'any_uppercase': check_any_uppercase(word),
                'all_uppercase': check_all_uppercase(word), 'any_special': check_any_special(word),
                'ascii': get_ascii_fraction(word), 'normalized_word': clean(word).lower()}

    features['suffix1'] = word[-1:]
    features['prefix1'] = word[:1] 

    features['suffix2'] = word[-2:]
    features['prefix2'] = word[:2]

    features['suffix3'] = word[-3:]
    features['prefix3'] = word[:3]

    return features

def sentence_features(sentence):
    features = []

    for i in range(len(sentence)):
        features.append(word_features(sentence, i))

    return features

def sentence_labels(sentence):
    all_labels = []

    for token in sentence:
        all_labels.append(token[2])

    return all_labels

In [ ]:
tweets_validation = tweets[int(len(tweets)*0.8):]
tweets = tweets[:int(len(tweets)*0.8)]
print(len(tweets_validation), len(tweets))

298 1191


In [ ]:
pip install python-crfsuite

In [ ]:
import pycrfsuite

# train model
k = 5
c1 = 0.0001
c2 = 0.1
chunk = int(len(tweets)/k)
results = []
all_test_predictions = []
all_test_ground_truth = []

for i in range(k):
    test_sentences = tweets[i*chunk:(i + 1)*chunk]
    train_sentences = tweets[:i*chunk] + tweets[(i + 1)*chunk:]

    # extracting training set
    X_train = [sentence_features(sentence) for sentence in train_sentences]
    y_train = [sentence_labels(sentence) for sentence in train_sentences]

    # extracting test set
    X_test = [sentence_features(sentence) for sentence in test_sentences]
    y_test = [sentence_labels(sentence) for sentence in test_sentences]

    # loading crf module
    trainer = pycrfsuite.Trainer(verbose=False)

    for X_sequence, y_sequence in zip(X_train, y_train):
        trainer.append(X_sequence, y_sequence)

    trainer.set_params({
        'c1': c1,   # coefficient for L1 penalty
        'c2': c2,  # coefficient for L2 penalty
        'max_iterations': 1000,  # stop earlier

        # include transitions that are possible, but not observed
        'feature.possible_transitions': True,
        'feature.possible_states' : True
    })

    # training
    trainer.train('pos_crf_' + str(i))

    # testing
    tagger = pycrfsuite.Tagger()
    tagger.open('pos_crf_' + str(i))

    y_pred = []

    for X_sequence in X_test:
        y_pred.append(tagger.tag(X_sequence))

    predicted_labels = []
    correct_labels = []

    for p in y_pred:
        for j in p:
            predicted_labels.append(j)
            all_test_predictions.append(j)

    for p in y_test:
        for j in p:
            correct_labels.append(j)
            all_test_ground_truth.append(j)

print(classification_report(all_test_ground_truth, all_test_predictions, digits = 4))

              precision    recall  f1-score   support

         ADJ     0.7300    0.6948    0.7119      1245
         ADP     0.9240    0.9298    0.9269      2379
         ADV     0.8537    0.7797    0.8150       808
        CONJ     0.9528    0.9029    0.9272       649
         DET     0.9110    0.8803    0.8954       919
        NOUN     0.8069    0.8396    0.8230      4047
         NUM     0.9621    0.8942    0.9269       312
        PART     0.8020    0.6941    0.7441      1144
    PART_NEG     0.9545    0.9869    0.9705       383
        PRON     0.9023    0.8592    0.8802      1172
     PRON_WH     0.9211    0.9238    0.9224       341
       PROPN     0.9076    0.9154    0.9115      2188
        VERB     0.8440    0.8902    0.8665      4826
           X     0.9921    0.9840    0.9880      5984

    accuracy                         0.8887     26397
   macro avg     0.8903    0.8696    0.8793     26397
weighted avg     0.8891    0.8887    0.8884     26397



In [ ]:
# validation
# extracting training set
X_train = [sentence_features(sentence) for sentence in tweets]
y_train = [sentence_labels(sentence) for sentence in tweets]

# extracting test set
X_test = [sentence_features(sentence) for sentence in tweets_validation]
y_test = [sentence_labels(sentence) for sentence in tweets_validation]

trainer = pycrfsuite.Trainer(verbose=False)

for X_sequence, y_sequence in zip(X_train, y_train):
    trainer.append(X_sequence, y_sequence)

trainer.set_params({
    'c1': c1,   # coefficient for L1 penalty
    'c2': c2,  # coefficient for L2 penalty
    'max_iterations': 1000,  # stop earlier

    # include transitions that are possible, but not observed
    'feature.possible_transitions': True,
    'feature.possible_states' : True
})

#training
trainer.train('pos_crf')

#testing
tagger = pycrfsuite.Tagger()
tagger.open('pos_crf')

all_test_predictions = []
all_test_ground_truth = []

y_pred = []

for X_sequence in X_test:
    y_pred.append(tagger.tag(X_sequence))

predicted_labels = []
correct_labels = []

for i in y_pred:
    for j in i:
        predicted_labels.append(j)
        all_test_predictions.append(j)

for i in y_test:
    for j in i:
        correct_labels.append(j)
        all_test_ground_truth.append(j)

print(classification_report(all_test_ground_truth, all_test_predictions, digits = 4))

              precision    recall  f1-score   support

         ADJ     0.7492    0.7492    0.7492       303
         ADP     0.9299    0.9468    0.9383       602
         ADV     0.8653    0.7877    0.8247       212
        CONJ     0.9542    0.9182    0.9359       159
         DET     0.9132    0.9009    0.9070       222
        NOUN     0.8256    0.8571    0.8411       994
         NUM     0.9710    0.8481    0.9054        79
        PART     0.8249    0.7465    0.7837       284
    PART_NEG     0.9659    1.0000    0.9827        85
        PRON     0.9375    0.8481    0.8905       283
     PRON_WH     0.9500    0.9620    0.9560        79
       PROPN     0.9265    0.9180    0.9222       549
        VERB     0.8586    0.9031    0.8803      1156
           X     0.9930    0.9831    0.9880      1593

    accuracy                         0.9024      6600
   macro avg     0.9046    0.8835    0.8932      6600
weighted avg     0.9033    0.9024    0.9024      6600



In [ ]:
X_test

[[{'all_uppercase': False,
   'any_special': True,
   'any_uppercase': True,
   'ascii': 1.0,
   'is_title': False,
   'language': 'rest',
   'prefix1': '@',
   'prefix2': '@A',
   'prefix3': '@Ar',
   'suffix1': 'l',
   'suffix2': 'al',
   'suffix3': 'wal',
   'word': '@ArvindKejriwal',
   'word_clean': 'arvindkejriwal',
   'word_length': 15},
  {'all_uppercase': False,
   'any_special': False,
   'any_uppercase': True,
   'ascii': 1.0,
   'is_title': True,
   'language': 'hi',
   'prefix1': 'K',
   'prefix2': 'Ko',
   'prefix3': 'Ko',
   'suffix1': 'o',
   'suffix2': 'Ko',
   'suffix3': 'Ko',
   'word': 'Ko',
   'word_clean': 'ko',
   'word_length': 2},
  {'all_uppercase': False,
   'any_special': False,
   'any_uppercase': True,
   'ascii': 1.0,
   'is_title': True,
   'language': 'hi',
   'prefix1': 'J',
   'prefix2': 'Jo',
   'prefix3': 'Jo',
   'suffix1': 'o',
   'suffix2': 'Jo',
   'suffix3': 'Jo',
   'word': 'Jo',
   'word_clean': 'jo',
   'word_length': 2},
  {'all_uppercase':

In [ ]:
y_pred

[['X',
  'ADP',
  'PRON',
  'NUM',
  'NOUN',
  'VERB',
  'VERB',
  'PRON',
  'ADJ',
  'NOUN',
  'VERB',
  'VERB',
  'PRON',
  'X',
  'DET',
  'NOUN',
  'VERB',
  'X',
  'X',
  'X',
  'X',
  'X'],
 ['PRON_WH',
  'PROPN',
  'VERB',
  'DET',
  'NOUN',
  'ADP',
  'DET',
  'ADJ',
  'NOUN',
  'NOUN',
  'X',
  'X',
  'X',
  'X'],
 ['X',
  'DET',
  'NOUN',
  'PROPN',
  'VERB',
  'ADV',
  'ADJ',
  'PART',
  'ADJ',
  'PROPN',
  'PART',
  'NOUN',
  'VERB',
  'VERB',
  'PART_NEG',
  'VERB',
  'VERB',
  'VERB',
  'X'],
 ['NOUN',
  'NOUN',
  'VERB',
  'ADP',
  'NOUN',
  'X',
  'DET',
  'NOUN',
  'NOUN',
  'ADP',
  'PRON_WH',
  'VERB',
  'X',
  'NOUN',
  'X',
  'PART',
  'VERB',
  'NUM',
  'PROPN',
  'CONJ',
  'VERB',
  'VERB',
  'X',
  'X',
  'X'],
 ['X',
  'X',
  'ADV',
  'ADJ',
  'X',
  'X',
  'VERB',
  'VERB',
  'ADV',
  'DET',
  'NOUN',
  'NOUN',
  'ADP',
  'X',
  'X',
  'PRON',
  'VERB',
  'VERB',
  'ADV',
  'VERB',
  'CONJ',
  'NOUN',
  'ADP',
  'NOUN',
  'VERB',
  'CONJ',
  'VERB',
  'PROPN']

In [ ]:
# sarcasm data
f2 = open('/content/drive/My Drive/Data Files/code-mixed analysis data/Sarcasm_tweets_with_language.txt', 'r')

tweets_sarcasm = []
temp = []

for line in f2:   
    line = line.strip()
    line = line.split(' ')
    line = [token.strip() for token in line if token != '' and  token != ' ' and token != '\n']

    if len(line) == 0:
        if len(temp) > 0:
            tweets_sarcasm.append(temp)
            temp = []
    elif len(line) == 1:
        continue
    else:
        temp.append(line)

tweets_sarcasm = np.array(tweets_sarcasm)
# np.random.seed(10)
# np.random.shuffle(tweets_sarcasm)
tweets_sarcasm = tweets_sarcasm.tolist()

In [ ]:
# prediction
X = [sentence_features(sentence) for sentence in tweets_sarcasm]

tagger = pycrfsuite.Tagger()
tagger.open('pos_crf')

y_pred = []

for X_sequence in X:
    y_pred.append(tagger.tag(X_sequence))

for i in y_pred:
    for j in i:
        tweets_sarcasm[i][j].append(y_pred[i][j])

# save to csv file
savetxt('/content/drive/My Drive/Data Files/code-mixed analysis data/POS.csv', tweets_sarcasm, delimiter=',')